## Using Gradio to create a simple interface.

Check out the library on [github](https://github.com/gradio-app/gradio-UI) and see the [getting started](https://gradio.app/getting_started.html) page for more demos.

We'll start with a basic function that greets an input name.

Now we'll wrap this function with a Gradio interface.

In [24]:
!pip install -q gradio

That's all! Go ahead and open that share link in a new tab. Check out our [getting started](https://gradio.app/getting_started.html) page for more complicated demos.

In [25]:
from google.colab import drive
drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


In [26]:
from keras.datasets import mnist
from keras.utils import np_utils
from keras.models import Sequential
from keras.layers import Dense,Activation

In [27]:
# import gradio
# gradio.Interface(greet, "text", "text").launch(share=True)
from keras.models import load_model
#import tensorflow as tf
# 替换自己的模型
#inception_net = tf.keras.applications.MobileNetV2()


In [28]:
from keras.models import load_model
import numpy as np
from keras.preprocessing import image
from keras.preprocessing.image import load_img
from PIL import ImageFilter
from PIL import Image
import cv2
import os

#PHOTO_SIZE = 120  #对图片大小进行限制，低于120KB的抛弃
#path = r'/content/sunny.jpg'  # 目标
weight_path = r'/content/drive/MyDrive/恶劣天气图像识别代码-毕业设计-戴一凡/basic.h5' #权重文件

#re_x =256  #输入到神经网络中的文件的大小

model = load_model(weight_path)
#img = Image.open(path)
#img = img.resize((re_x,re_x), Image.ANTIALIAS) #缩放到事先指定的大小
#img = np.expand_dims(img, axis=0)
#print(img)
#inception_net=model.predict(img)#获取预测值


In [29]:
#labels =['Srainy', 'Mrainy', 'Lrainy', 'Sfoggy', 'Mfoggy','Lfoggy','sunny']
labels=['天气:小雨，  降雨强度(mm/min):0.8，  能见度(m):500，  道路摩擦系数:0.64,  限速(km/h):80',
    '天气:中雨，  降雨强度(mm/min):1.2，  能见度(m):250，  道路摩擦系数:0.58,  限速(km/h):50',
    '天气:大雨，  降雨强度(mm/min):1.6，  能见度(m):50-150， 道路摩擦系数:0.45,  限速(km/h):30',
    '天气:薄雾，  降雨强度(mm/min):0，   能见度(m):500:，  道路摩擦系数:0.8,  限速(km/h):110',
    '天气:大雾，  降雨强度(mm/min):0，   能见度(m):200，   道路摩擦系数:0.8,  限速(km/h):70',
    '天气:浓雾，  降雨强度(mm/min):0:，   能见度(m):50-100， 道路摩擦系数:0.8,  限速(km/h):40',
    '天气:晴，   降雨强度(mm/min):0，   能见度(m):>1000:，  道路摩擦系数:0.8,  限速(km/h):120']
def classify_image(inp):
  inp = inp.resize((256,256), Image.ANTIALIAS) #缩放到事先指定的大小
  inp = np.expand_dims(inp, axis=0)
  prediction = model.predict(inp)
  confidences = {labels[i]: float(prediction[0][i]) for i in range(7)}
  return confidences
#path = r'/content/rainy.jpg'

#img = Image.open(path)
#print(classify_image(img))

In [36]:
import gradio as gr
gr.Interface(
    fn=classify_image,
    inputs=gr.Image(type="pil",shape=(256,256)),
    outputs=gr.Label(num_top_classes=1),
    examples=["rainy.jpg", "sunny.jpg"],
    interpretation="default",cache_examples=True,title="恶劣天气图像识别与预警"
).launch(enable_queue=True)

Caching examples at: '/content/gradio_cached_examples/66/log.csv'
Colab notebook detected. To show errors in colab notebook, set `debug=True` in `launch()`
Running on public URL: https://18698.gradio.app

This share link expires in 72 hours. For free permanent hosting, check out Spaces: https://huggingface.co/spaces


(<gradio.routes.App at 0x7f839f968d50>,
 'http://127.0.0.1:7862/',
 'https://18698.gradio.app')

In [ ]:
import gradio as gr
def generate_mutimodal(title, context, senti, num, img):
    return f"Title:{title}\nContext:{context}\nSenti:{senti}\nNum:{num}...{img}"
    
server = gr.Interface(
    fn=generate_mutimodal, 
    inputs=[
        gr.Textbox(lines=1, placeholder="请输入标题", label="标题", interactive=True),  # interactive指定该组件是否允许用户输入或者交互
        gr.Textbox(lines=2, placeholder="请输入正文", label="正文"),
        gr.Radio(["0", "1", "随机"], label="倾向"),
        gr.Number(label='条数'),
        gr.Image(shape=(200, 200),  label="请上传图片(可选)").style(height='24', rounded=True)
    ], 
    outputs="text",
    examples=[
        ["标题1", "正文1", "0", None],
        ["标题2", "正文2", "随机"],
    ],
    title="可控文本生成",
    description="标题和正文至少一个非空，图片可选是否上传",
    article="""
        ### 这里是底部的article
        #### article 1
        This is article 1
    """,
    css="body {background-color: red; font-size: large}",
    allow_flagging="never",     # 输出侧是否开启flag功能 比如让用户去标记输出结果是否正确 写到日志
    live=False,                 # live: 用户输入改变时是否自动计算结果
    cache_examples=False,       # cache_examples: 是否将example里的结果提前算好存到缓存里
)

server.launch(
    enable_queue=False,         # enable_queue: 如果app流量很大，需设置参数以防止超时。这将使用长轮询对调用进行排队，一次仅处理一个调用。长轮询还可以防止网络超时，因此，如果函数的推理时间很长（> 1 分钟），则应使用队列。
    auth=("admin", "admin"),    # auth: 参数值可以是 (user, pwd) 的元组，也可以是一个函数名（用户名和密码是参数, 并返回 True/False）。enable_queue=True 时，auth不能传元组。
    share=True                 # share: 可生成 72h 的公网访问地址，原理相当于 gradio 提供了一个内网穿透的代理，并没有把代码+环境上传到他们服务器
)


/usr/local/lib/python3.7/dist-packages/gradio/components.py:197: UserWarning: 'rounded' styling is no longer supported. To round adjacent components together, place them in a Column(variant='box').
  "'rounded' styling is no longer supported. To round adjacent components together, place them in a Column(variant='box')."


Colab notebook detected. To show errors in colab notebook, set `debug=True` in `launch()`
Running on public URL: https://17915.gradio.app

This share link expires in 72 hours. For free permanent hosting, check out Spaces: https://huggingface.co/spaces


(<gradio.routes.App at 0x7f9d6e3bfb10>,
 'http://127.0.0.1:7861/',
 'https://17915.gradio.app')